In [1]:
import json
import logging
import faster_coco_eval
from faster_coco_eval import COCO, COCOeval_faster
from faster_coco_eval.extra import Curves

print(f"{faster_coco_eval.__version__=}")

logging.root.setLevel("INFO")
logging.debug("Запись.")

faster_coco_eval.__version__='1.5.5'


In [2]:
prepared_coco_in_dict = COCO.load_json("../tests/synth_test_dataset/test.json")
prepared_anns = COCO.load_json("../tests/synth_test_dataset/result_data.json")

In [3]:
iouType = "keypoints"

In [4]:
cocoGt = COCO(prepared_coco_in_dict)
cocoDt = cocoGt.loadRes(prepared_anns)

cocoEval = COCOeval_faster(
    cocoGt, cocoDt, iouType, extra_calc=True, kpt_oks_sigmas=[0.01] * 4
)

cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()

In [5]:
cocoEval.stats_as_dict

{'AP_all': 0.8877048841154976,
 'AP_50': 1.0,
 'AP_75': 1.0,
 'AP_medium': -1.0,
 'AP_large': 0.8877048841154976,
 'AR_all': 0.9267605633802816,
 'AR_second': 1.0,
 'AR_third': 1.0,
 'AR_medium': -1.0,
 'AR_large': 0.9267605633802816,
 'mIoU': 0.9378257896663419,
 'mAUC_50': 1.0}

In [6]:
cur = Curves(cocoGt, cocoDt, iouType=iouType, kpt_oks_sigmas=[0.025] * 4)

cur.plot_ced_metric()
cur.plot_f1_confidence()

In [7]:
from faster_coco_eval.extra import PreviewResults

preview = PreviewResults(cur.cocoGt, cur.cocoDt, iouType=iouType, kpt_oks_sigmas=[0.01] * 4)

In [8]:
imgs = []

for img_id, anns in cur.cocoDt.img_ann_map.items():
    for ann in anns:
        if ann.get("mae", 0) > 3.5:
            imgs.append([img_id, ann.get("mae", 0)])

imgs.sort(key=lambda x: x[1], reverse=True)
print(imgs)

imgs = [i[0] for i in imgs]
imgs

[[3966, 4.620729166666656], [3848, 4.237343749999997], [4022, 3.8133333333333326], [3816, 3.8036979166666605]]


[3966, 3848, 4022, 3816]

In [9]:
preview.display_tp_fp_fn(
    data_folder="../tests/synth_test_dataset/",
    image_ids=imgs,
    display_gt=True,
)